# Projekt - Test t studenta

- Marcin Kostrzewski
- Krystian Wasilewski
- Mateusz Tylka

## Test t studenta

Metoda statystyczna służącą do porównania dwóch średnich między sobą gdy znamy liczbę badanych próbek, średnią arytmetyczną oraz wartość odchylenia standardowego lub wariancji.
Jest to jeden z mniej skomplikowanych i bardzo często wykorzystywanych testów statystycznych używanych do weryfikacji hipotez. Dzięki niemu możemy dowiedzieć się czy dwie różne średnie są różne niechcący (w wyniku przypadku) czy są różne istotnie statystycznie (np. z uwagi na naszą manipulację eksperymentalna).
Wyróżniamy 3 wersję testu t:

1. test t Studenta dla jednej próby
2. test t Studenta dla prób niezależnych
3. test t Studenta dla prób zależnych

Wszystkie rodzaje testów są testami parametrycznymi, a co za tym idzie nasze mierzone zmienne ilościowe powinny mieć rozkład normalny.

In [313]:
import numpy as np
import pandas as pd
from enum import Enum
from math import sqrt
from scipy import stats
from scipy.stats import sem
from scipy.stats import t
import matplotlib.pyplot as plt
from statistics import mean, stdev
from scipy.stats import ttest_ind, ttest_1samp, ttest_rel

In [314]:
dataset = pd.read_csv('experiment_data.csv')

In [315]:
class Alternatives(Enum):
    LESS = 'less'
    GREATER = 'greater'

In [316]:
def calculate_t_difference(t_stat_sample, t_stat_list, alternative):
    """
    Funkcja oblicza procent statystyk testowych powstałych z prób bootstrapowych, 
    które róznią się od statystyki testowej powstałej ze zbioru według hipotezy alternatywnej.
    """
    all_stats = len(t_stat_list)
    stats_different_count = 0
    for t_stat_boot in t_stat_list:
        if alternative is Alternatives.LESS and t_stat_boot < t_stat_sample:
            stats_different_count += 1 
        elif alternative is Alternatives.GREATER and t_stat_boot > t_stat_sample:
            stats_different_count += 1
    return stats_different_count / all_stats

In [317]:
def t_test_1_samp(sample_1, population_mean=None, alternative=Alternatives.LESS):
    """
    Funkcja przeprowadza test T-studenta dla jednej zmiennej.
    """
    t_stat_from_sample, _ = ttest_1samp(a=sample_1, popmean=population_mean, alternative=alternative.value)
    t_stat_list = get_t_stats(sample_1, t_stat_fn=ttest_1samp, alternative=alternative, population_mean=population_mean)

    p = calculate_t_difference(t_stat_from_sample, t_stat_list, alternative)

    return p, t_stat_list

In [318]:
def t_test_ind(sample_1, sample_2, alternative=Alternatives.LESS):
    """
    Funkcja przeprowadza test T-studenta dla dwóch zmiennych niezależnych.
    """
    t_stat_from_sample, _ = ttest_ind(sample_1, sample_2, alternative=alternative.value)
    t_stat_list = get_t_stats(sample_1, sample_2, alternative=alternative, t_stat_fn=ttest_ind)

    p = calculate_t_difference(t_stat_from_sample, t_stat_list, alternative)

    return p, t_stat_list

In [319]:
def t_test_dep(sample_1, sample_2, alternative=Alternatives.LESS):
    """
    Funkcja przeprowadza test T-studenta dla dwóch zmiennych zależnych.
    """
    t_stat_list = get_t_stats(sample_1, sample_2, alternative=alternative, t_stat_fn=ttest_rel)
    t_stat_from_sample, _ = ttest_rel(sample_1, sample_2, alternative=alternative.value)

    p = calculate_t_difference(t_stat_from_sample, t_stat_list, alternative)

    return p, t_stat_list

In [320]:
def get_t_stats(sample_1, sample_2=None, t_stat_fn=ttest_1samp, alternative=Alternatives.LESS, population_mean=None):
    """Funkcja oblicza listę statystyk testowych dla każdej próbki bootstrapowej wybranej na podstawie danych sample_1 i sample_2"""
    t_stat_list = []

    # One sample test
    if t_stat_fn is ttest_1samp and sample_2 is None:
        if not population_mean:
            raise Exception("population_mean not provided")
        for bootstrap in generate_bootstraps(sample_1):
            stat, _ = t_stat_fn(bootstrap, population_mean, alternative=alternative.value)
            t_stat_list.append(stat)
        return t_stat_list

    # Two sample test
    for bootstrap_sample in generate_bootstraps(pd.concat((sample_1, sample_2))):
        bootstrap_1, bootstrap_2 = bootstrap_sample.iloc[: round(len(bootstrap_sample) * 0.5)], bootstrap_sample.iloc[: round(-len(bootstrap_sample) * 0.5)]
        stat, _ = t_stat_fn(bootstrap_1, bootstrap_2, alternative=alternative.value)
        t_stat_list.append(stat)
    return t_stat_list

## Test Shapiro Wilka

Wszystkie rodzaje testów są testami parametrycznymi, a co za tym idzie nasze mierzone zmienne ilościowe powinny mieć rozkład normalny.

## Testowanie hipotez metodą bootstrap

**Bootstrap** – metoda szacowania (estymacji) wyników poprzez wielokrotne losowanie ze zwracaniem z próby. Polega ona na utworzeniu nowego rozkładu wyników, na podstawie posiadanych danych, poprzez wielokrotne losowanie wartości z posiadanej próby. Metoda ze zwracaniem polega na tym, że po wylosowaniu danej wartości, “wraca” ona z powrotem do zbioru.

Metoda bootstrapowa znajduje zastosowanie w sytuacji, w której nie znamy rozkładu z populacji z której pochodzi próbka lub w przypadku rozkładów małych lub asymetrycznych. W takim wypadku, dzięki tej metodzie, wyniki testów parametrycznych i analiz opartych o modele liniowe są bardziej precyzyjne. Zazwyczaj losuje się wiele próbek, np. 2000 czy 5000.

In [321]:
def generate_bootstraps(data, n_bootstraps=100):
    data_size = data.shape[0]
    for _ in range(n_bootstraps):
        indices =  np.random.choice(len(data), size=data_size)
        yield data.iloc[indices, :]

## Test t studenta dla jednej próby

**Test t Studenta dla jednej próby** wykorzystujemy gdy chcemy porównać średnią “teoretyczną” ze średnią, którą faktycznie możemy zaobserwować w naszej bazie danych. Średnia teoretyczna to średnia pochodząca z innych badań lub po prostu bez większych uzasadnień pochodząca z naszej głowy.

Wyobraźmy sobie, że mamy dane z takimi zmiennymi jak wzrost pewnej grupy ludzi. Dzięki testowi t Studenta dla jednej próby możemy dowiedzieć się np. czy wzrost naszego młodszego brata wynoszący 155cm odbiega znacząco od średniej wzrostu tej grupy. Hipoteza zerowa w takim badaniu wyglądałaby następująco H0: Badana próba została wylosowana z populacji, w której wzrost osób wynosi średnio 155cm. Z kolei hipoteza alternatywna będzie brzmiała H1: Badana próba nie została wylosowana z populacji gdzie średni wzrost wynosi 155cm


In [322]:
def bootstrap_one_sample(sample, population_mean, alternative=Alternatives.LESS):
    return t_test_1_samp(
        sample_1=sample,
        population_mean=population_mean,
        alternative=alternative,
    )

### Sprawdzenie czy osoba o wzroście 165cm pasuje do populacji (nie jest odmieńcem)

In [323]:
dummy = pd.DataFrame([1, 2, 3, 4, 5])
dummy2 = pd.DataFrame([4, 5, 6, 7, 8])
dummy3 = pd.DataFrame([1, 3 , 3, 4, 6])

In [324]:
#TODO: poprawić kod aby można było podawać kolumny

p, _ = bootstrap_one_sample(dummy, 165)
print(f'p: {p}')

p: 0.73


TODO: Wniosek

## Test t studenta dla prób niezależnych

**Test t Studenta dla prób niezależnych** jest najczęściej stosowaną metodą statystyczną w celu porównania średnich z dwóch niezależnych od siebie grup. Wykorzystujemy go gdy chcemy porównać dwie grupy pod względem jakiejś zmiennej ilościowej. Na przykład gdy chcemy porównać średni wzrost kobiet i mężczyzn w danej grupie.

Zazwyczaj dwie średnie z różnych od siebie grup będą się różnić. Test t Studenta powie nam jednak czy owe różnice są istotne statystycznie – czy nie są przypadkowe. Hipoteza zerowa takiego testu będzie brzmiała H0: Średni wzrost w grupie mężczyzn jest taki sam jak średni w grupie kobiet. Hipoteza alternatywna z kolei H1: Kobiety będą różnić się od mężczyzn pod wzrostu.
Jeśli wynik testu t Studenta będzie istotny na poziomie p < 0,05 możemy odrzucić hipotezę zerową na rzecz hipotezy alternatywnej.


In [325]:
def bootstrap_independent(sample_1, sample_2, alternative=Alternatives.LESS):
    return t_test_ind(
        sample_1=sample_1,
        sample_2=sample_2,
        alternative=alternative,
    )

# TODO: Wyciągnąć wysokości kobiet i mężczyzn oraz poprawić kod aby można było podawać kolumny
t_stat, df, cv, p, _ = bootstrap_independent(dataset, dataset)
pretty_print_full_stats(t_stat, df, cv, p)

TODO: Wniosek

## Test t studenta dla prób zależnych

W odróżnieniu od testu t – Studenta dla prób niezależnych, gdzie porównujemy dwie grupy, ten rodzaj testu stosujemy gdy poddajemy analizie tą samą pojedynczą grupę, ale dwukrotnie w czasie. Na przykład gdy chcemy porównać średnie wagi grupy osób przed dietą oraz po diecie, aby sprawdzić czy dieta spowodowała istotne zmiany statystyczne.

Hipoteza zerowa takiego testu będzie brzmiała H0: Średnia waga osób po diecie jest taka sama jak przed dietą. Hipoteza alternatywna z kolei H1: Dieta znacząco wpłynęła na średnią wagę danej grupy.

In [326]:
def bootstrap_dependent(sample_1, sample_2, alternative=Alternatives.LESS):
    return t_test_dep(
        sample_1=sample_1,
        sample_2=sample_2,
        alternative=alternative,
    )

# TODO: Wyciągnąć wagi przed dietą i po oraz poprawić kod aby można było podawać kolumny
t_stat, df, cv, p, _ = bootstrap_dependent(dataset, dataset)
pretty_print_full_stats(t_stat, df, cv, p)

TODO: Wniosek

## Wykresy

In [327]:
def draw_distribution(stats):
    """
    Funkcja rysuje rozkład statystyki testowej
    @param stats: lista statystyk testowych
    """
    plt.hist(stats)
    plt.xlabel('Test statistic value')
    plt.ylabel('Frequency')
    plt.show()

## Testy

In [328]:
# Testy z bootstrappowaniem


print('Statystyki dla jednej próby:')
p, _ = bootstrap_one_sample(dummy, 2)
print(f'p {p}')

print('Statystyki dla dwóch prób zależnych:')
p, _ = bootstrap_dependent(dummy2, dummy3)
print(f'p {p}')

print('Statystyki dla dwóch prób niezależnych:')
p, _ = bootstrap_independent(dummy2, dummy3)
print(f'p {p}')

Statystyki dla jednej próby:
0.44
Statystyki dla dwóch prób zależnych:
0.0
Statystyki dla dwóch prób niezależnych:
1.0
